# 이미지 인식의 꽃, 컨볼루션 신경망(CNN)


---

각 내용의 주석을 보시고, 주석과 코드 작성을 완료하여 Tistory에 업로드해주세요!

In [ ]:
# 필요한 라이브러리 임포트
import numpy as np
import matplotlib.pyplot as plt
from tensorflow.keras.datasets import mnist
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Dropout, Flatten, Conv2D, MaxPooling2D
from tensorflow.keras.callbacks import ModelCheckpoint, EarlyStopping
from tensorflow.keras.utils import to_categorical

# 데이터 불러오기
(X_train, y_train), (X_test, y_test) = mnist.load_data()

# 데이터 전처리
#차원 변환 과정
X_train= X_train.reshape(X_train.shape[0],28,28,1)
X_test = X_test.reshape(X_test.shape[0],28,28,1)
#데이터 타입 실수형 변환
X_train = X_train.astype('float64')
X_test = X_test.astype('float64')

#정규화 과정
X_train=X_train/255.0
X_test=X_test/255.0

# 레이블 원-핫 인코딩
y_train=to_categorical(y_train,10)
y_test=to_categorical(y_test,10)

# 컨볼루션 신경망(CNN) 모델 구성
# 각 층이 뭘 의미하는지 주석으로 적어보기!
model = Sequential()
model.add(Conv2D(32, kernel_size=(3, 3), activation='relu', input_shape=(28, 28, 1))) #컨볼루션 층
model.add(Conv2D(64, (3, 3), activation='relu'))
model.add(MaxPooling2D(pool_size=(2, 2))) #맥스 풀링을 사용하는 풀링
model.add(Dropout(0.25)) #과적합을 피하는 드롭아웃 (25% 노드 드랍)
model.add(Flatten()) #이미지를 2차원으로 다루게 함
model.add(Dense(128, activation='relu'))
model.add(Dropout(0.5))
model.add(Dense(10, activation='softmax'))




In [ ]:
# 모델 컴파일
model.compile(loss='categorical_crossentropy',
              optimizer = 'adam',
              metrics=['accuracy'] )

# 모델 저장 및 조기 종료 설정
modelpath="./Minist_CNN.keras"
checkpointer = ModelCheckpoint(filepath=modelpath, monitor='val_loss', verbose=1, save_best_only=True)

early_stopping_callback=EarlyStopping(monitor='val_loss',patience=10)

# 모델 학습
history=model.fit(X_train,y_train,validation_split=0.25,epochs=30,batch_size=200,verbose=0,
                  callbacks=[early_stopping_callback,checkpointer])


# 테스트셋 평가
print('\n Test Accuracy : %.4f'%(model.evaluate(X_test,y_test)[1]))




# 영화를 보고 남긴 리뷰를 딥러닝 모델로 학습

---
주석을 보고 코드 작성을 완료하여 Tistory에 업로드해주세요!


In [ ]:
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense,Flatten,Embedding
from tensorflow.keras.utils import to_categorical
from numpy import array

# 텍스트 리뷰 자료를 지정합니다.
docs = ["너무 재밌네요","최고예요","참 잘 만든 영화예요","추천하고 싶은 영화입니다","한번 더 보고싶네요","글쎄요","별로예요","생각보다 지루하네요","연기가 어색해요","재미없어요"]

# 긍정 리뷰는 1, 부정 리뷰는 0으로 클래스를 지정합니다.
classes = array([1,1,1,1,1,0,0,0,0,0])

# 토큰화
token = Tokenizer()
token.fit_on_texts(docs)
print(token.word_index)
x= token.texts_to_sequences(docs)

In [ ]:
# 패딩
padded_x=pad_sequences(x,4)
word_size=len(token.word_index)+1

# 모델 만들기
model = Sequential()
model.add(Embedding(word_size,8,input_length=4))
model.add(Flatten())
model.add(Dense(1,activation='sigmoid'))
model.summary()

model.compile(optimizer='adam', loss = 'binary_crossentropy',metrics=['accuracy'])
model.fit(padded_x,classes,epochs=20)
print("\n Accuracy:%.4f"%(model.evaluate(padded_x,classes)[1]))
